# YOLO Sigma-Delta Neural Network (SDNN) Training


In [1]:
import os
from datetime import datetime
from typing import Any, Dict, Tuple
import numpy as np
import torch
import yaml
from lava.lib.dl import slayer
from torch.utils.data import DataLoader

from lava.lib.dl.slayer.object_detection.boundingbox.metrics import APstats
from lava.lib.dl.slayer.object_detection.boundingbox.utils import create_video
from lava.lib.dl.slayer.object_detection.boundingbox.utils import non_maximum_suppression as nms
from lava.lib.dl.slayer.object_detection.dataset.bdd100k import BDD
from lava.lib.dl.slayer.object_detection.yolo_base import YOLOtarget
from lava.lib.dl.slayer.object_detection.models.tiny_yolov3_str import Network

# Load Inference parameters

In [2]:
class dotdict(dict):
    """dot.notation access to dictionary attributes"""
    __getattr__ = dict.get
    __setattr__ = dict.__setitem__
    __delattr__ = dict.__delitem__

args = dotdict(load='trained/network.pt')
trained_folder = os.path.dirname(args.load)
print(trained_folder)

with open(trained_folder + '/args.txt', 'rt') as f:
    model_args = dotdict(yaml.safe_load(f))
    for (k, v) in model_args.items():
        if k not in args.keys():
            args[k] = v
            
print('Using GPUs {}'.format(args.gpu))
device = torch.device('cuda:{}'.format(args.gpu[0]))
classes_output = {'BDD100K': 11}
print(args)

trained
Using GPUs [0]
{'load': 'trained/network.pt', 'alpha_iou': 0.25, 'aug_prob': 0.2, 'b': 2, 'clip': 10, 'dataset': 'BDD100K', 'epoch': 50, 'exp': None, 'gpu': [0], 'label_smoothing': 0.1, 'lambda_cls': 1.0, 'lambda_coord': 1.0, 'lambda_iou': 1.0, 'lambda_noobj': 10.0, 'lambda_obj': 5.0, 'lr': 0.001, 'lrf': 0.001, 'num_workers': 1, 'output_dir': '.', 'path': '/home/lecampos/data/bdd100k', 'scale_grad': 0.2, 'seed': 'None', 'subset': False, 'tau_grad': 0.1, 'tgt_iou_thr': 0.5, 'threshold': 0.1, 'track_iter': 1000, 'warmup': 10, 'wd': '1e-05', 'clamp_max': 5.0}


# Load Network Parameters

In [3]:
if len(args.gpu) == 1:
        net = Network(threshold=model_args.threshold,
                        tau_grad=model_args.tau_grad,
                        scale_grad=model_args.scale_grad,
                        num_classes=classes_output[model_args.dataset],
                        clamp_max=model_args.clamp_max).to(device)
        module = net
else:
        net = torch.nn.DataParallel(Network(threshold=model_args.threshold,
                                        tau_grad=model_args.tau_grad,
                                        scale_grad=model_args.scale_grad,
                                        num_classes=classes_output[model_args.dataset],
                                        clamp_max=model_args.clamp_max).to(device),
                                device_ids=args.gpu)
        module = net.module


module.init_model((448, 448))
module.load_state_dict(torch.load(args.load))

yolo_target = YOLOtarget(anchors=net.anchors,
                             scales=net.scale,
                             num_classes=net.num_classes,
                             ignore_iou_thres=model_args.tgt_iou_thr)

# Load Dataset and Dataloader

In [4]:
test_set = BDD(root=args.path, dataset='track', train=False, randomize_seq=False, seq_len=60)

test_loader = DataLoader(test_set,
                        batch_size=args.b,
                        shuffle=True,
                        collate_fn=yolo_target.collate_fn,
                        num_workers=args.num_workers,
                        pin_memory=True)

# Run Inference

In [5]:
epoch = 0
stats = slayer.utils.LearningStats(accuracy_str='AP@0.5')
t_st = datetime.now()
ap_stats = APstats(iou_threshold=0.5)
all_counts = []
for i, (inputs, targets, bboxes) in enumerate(test_loader):
    net.eval()

    with torch.no_grad():
        inputs = inputs.to(device)
        predictions, counts = net(inputs)
        all_counts.append(counts.cpu().data.numpy())

        T = inputs.shape[-1]
        
        predictions = [nms(predictions[..., t]) for t in range(T)]

        for t in range(T):
            ap_stats.update(predictions[t], bboxes[t])

        # stats.testing.loss_sum += loss.item() * inputs.shape[0]
        stats.testing.num_samples += inputs.shape[0]
        stats.testing.correct_samples = ap_stats[:] * stats.testing.num_samples

        processed = i * test_loader.batch_size
        total = len(test_loader.dataset)
        time_elapsed = (datetime.now() - t_st).total_seconds()
        samples_sec = time_elapsed / (i + 1) / test_loader.batch_size
        header_list = [f'Test: [{processed}/{total} '
                        f'({100.0 * processed / total:.0f}%)]']
        header_list += ['Event Rate: ['
                        + ', '.join([f'{c.item():.2f}'
                                        for c in counts[0]]) + ']']
        stats.print(epoch, i, samples_sec, header=header_list)


Test: [0/200 (0%)]
Event Rate: [0.25, 0.16, 0.18, 0.22, 0.23, 0.20, 0.22, 0.24, 0.21, 0.18, 0.19, 0.50, 0.20, 0.19, 0.19, 0.22, 0.50, 0.22]
Epoch    0: i =     0 ,    5339.8045 ms elapsed        
Train  
Test  loss =     0.00000                          AP@0.5 = 0.22756 

Test: [2/200 (1%)]
Event Rate: [0.19, 0.12, 0.14, 0.17, 0.20, 0.19, 0.20, 0.22, 0.20, 0.17, 0.18, 0.50, 0.20, 0.18, 0.18, 0.20, 0.50, 0.22]
Epoch    0: i =     1 ,    5101.2370 ms elapsed        
Train  
Test  loss =     0.00000                          AP@0.5 = 0.23982 

Test: [4/200 (2%)]
Event Rate: [0.23, 0.15, 0.17, 0.20, 0.22, 0.20, 0.21, 0.23, 0.21, 0.18, 0.19, 0.50, 0.20, 0.19, 0.19, 0.21, 0.50, 0.22]
Epoch    0: i =     2 ,    4739.6533 ms elapsed        
Train  
Test  loss =     0.00000                          AP@0.5 = 0.23455 

Test: [6/200 (3%)]
Event Rate: [0.23, 0.14, 0.14, 0.17, 0.19, 0.17, 0.20, 0.21, 0.18, 0.17, 0.17, 0.50, 0.20, 0.17, 0.17, 0.20, 0.49, 0.23]
Epoch    0: i =     3 ,    4674.7291 ms 

# Results: Output vs groundtruth

In [13]:
from IPython.display import Video

BOX_COLOR_MAP = [(np.random.randint(256),
                  np.random.randint(256),
                  np.random.randint(256))
                 for _ in range(classes_output[args.dataset])]

create_video(inputs, bboxes, predictions, 'trained/test', BOX_COLOR_MAP, test_set.classes)

Video("./trained/test.mp4", embed=True)
